In [1]:
import sys
import os

sys.path.append(os.path.abspath("../src"))
PROJECT_ROOT = os.getenv("PROJECT_ROOT")

In [2]:
from recommender.data_processors.mastery_features_processor import MasteryFeaturesProcessor
from recommender.data_loaders.summoner_match_loader import SummonerMatchLoader
from recommender.utils.riot_api_helper import RiotApiHelper
from recommender.utils.map_helper import MapHelper
from recommender.utils.data_utils import ChampionsFeaturesDataset
from recommender.utils.data_utils import MultiEpochsDataLoader
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OrdinalEncoder
from recommender.filters.two_tower import TwoTowerModel, TwoTowerRecommender

mfp = MasteryFeaturesProcessor()
rah = RiotApiHelper()
sml = SummonerMatchLoader()
mh = MapHelper()

In [3]:
# champ_metadata = mh.get_lolstaticdata_champ_id_mapping()
# champ_metadata["Nidalee"]
# # Q W E R cd? 

In [4]:
# import pandas as pd 
# s = pd.DataFrame(champ_metadata)
# s.T["positions"]

In [5]:
puuid = "--EEhXPKpjfGXqRUXQeFUIrad-z3jgjyrwQj6Z49G4zWAK77gXCckScrJ9yxTxy91DXiJXWp_ka1Vg"

In [52]:
ttr = TwoTowerRecommender()
s = await mfp.async_load_encoded_ratings()
df = s[0]

In [53]:
import pandas as pd
from sklearn.preprocessing import MultiLabelBinarizer
list_cols = ["champ_positions", "champ_roles"]
mlb = MultiLabelBinarizer()
for list_col in list_cols:
    position_onehot = pd.DataFrame(
        mlb.fit_transform(df[list_col]),
        columns=[f"{list_col}_{cls}" for cls in mlb.classes_],
        index=df.index,
    )
    df = pd.concat([df.drop(columns=[list_col]), position_onehot], axis=1)

In [54]:
df

puuid champ_name  \
0       --EEhXPKpjfGXqRUXQeFUIrad-z3jgjyrwQj6Z49G4zWAK...     Aatrox   
1       -0tFbkE3vD6takqkFfPNO0xIRQsE-5GeKCJEBRYGwi04RT...     Aatrox   
2       -7e5FbjuTrjsYyDu8GQG0p9wORit7_GD7BHCxR-k9rNo6c...     Aatrox   
3       -AeAsdpxcfQCzruP8eiXWNoatCvBehRa4jQHi8EwcOS-o2...     Aatrox   
4       -Bb1a-1E8rA-pPj9Ox4CMqD9HFhUc621aLpnJCb-L0uHMH...     Aatrox   
...                                                   ...        ...   
146195  _vuXUF_TQs1RuindiNch6El_TrJX9b609fJGbXH64046v3...     Yorick   
146196  _wcrNrVvGYv3syJjVhNZx93SZJOwl3GYn0vK3oOxQb-0Jh...     Yorick   
146197  _xGyR0kT2240JuSOwzokb0ewFGVR3VeeGNJMBsYk3oU6Di...     Yorick   
146198  _Xuv4oW8ZMrsulBBFw8neDnnzf517VhDK9gKsGzUHG5YnS...     Yorick   
146199  _zI3Jacjq9-EgA4Nk-ZSO7KIzac3dgnFEu-qtO-11hBr7L...     Yorick   

          rating  user_id  champ_id summoner_rank summoner_lane  \
0       8.859117        0         0       DIAMOND        MIDDLE   
1       2.290347        1         0   GRANDMASTER        MIDDLE   
2       0.000000        2         0       DIAMOND        JUNGLE   
3       6.300402        3         0       DIAMOND        MIDDLE   
4       5.728852        5         0        MASTER        JUNGLE   
...          ...      ...       ...           ...           ...   
146195  1.861314      501       161   GRANDMASTER           TOP   
146196  0.000000      502       161    CHALLENGER       SUPPORT   
146197  0.000000      503       161       DIAMOND       SUPPORT   
146198  3.870494      495       161       DIAMOND        JUNGLE   
146199  0.000000      504       161    CHALLENGER        MIDDLE   

       champ_adaptive_type champ_attack_type champ_resource  ...  \
0          PHYSICAL_DAMAGE             MELEE     BLOOD_WELL  ...   
1          PHYSICAL_DAMAGE             MELEE     BLOOD_WELL  ...   
2          PHYSICAL_DAMAGE             MELEE     BLOOD_WELL  ...   
3          PHYSICAL_DAMAGE             MELEE     BLOOD_WELL  ...   
4          PHYSICAL_DAMAGE             MELEE     BLOOD_WELL  ...   
...                    ...               ...            ...  ...   
146195     PHYSICAL_DAMAGE             MELEE           MANA  ...   
146196     PHYSICAL_DAMAGE             MELEE           MANA  ...   
146197     PHYSICAL_DAMAGE             MELEE           MANA  ...   
146198     PHYSICAL_DAMAGE             MELEE           MANA  ...   
146199     PHYSICAL_DAMAGE             MELEE           MANA  ...   

        champ_roles_FIGHTER  champ_roles_JUGGERNAUT  champ_roles_MAGE  \
0                         1                       1                 0   
1                         1                       1                 0   
2                         1                       1                 0   
3                         1                       1                 0   
4                         1                       1                 0   
...                     ...                     ...               ...   
146195                    1                       1                 0   
146196                    1                       1                 0   
146197                    1                       1                 0   
146198                    1                       1                 0   
146199                    1                       1                 0   

        champ_roles_MARKSMAN  champ_roles_SKIRMISHER  champ_roles_SPECIALIST  \
0                          0                       0                       0   
1                          0                       0                       0   
2                          0                       0                       0   
3                          0                       0                       0   
4                          0                       0                       0   
...                      ...                     ...                     ...   
146195                     0                       0                       0   
146196                     0                    

In [55]:
df.columns

Index(['puuid', 'champ_name', 'rating', 'user_id', 'champ_id', 'summoner_rank',
       'summoner_lane', 'champ_adaptive_type', 'champ_attack_type',
       'champ_resource', 'champ_positions_BOTTOM', 'champ_positions_JUNGLE',
       'champ_positions_MIDDLE', 'champ_positions_SUPPORT',
       'champ_positions_TOP', 'champ_roles_ARTILLERY', 'champ_roles_ASSASSIN',
       'champ_roles_BATTLEMAGE', 'champ_roles_BURST', 'champ_roles_CATCHER',
       'champ_roles_DIVER', 'champ_roles_ENCHANTER', 'champ_roles_FIGHTER',
       'champ_roles_JUGGERNAUT', 'champ_roles_MAGE', 'champ_roles_MARKSMAN',
       'champ_roles_SKIRMISHER', 'champ_roles_SPECIALIST',
       'champ_roles_SUPPORT', 'champ_roles_TANK', 'champ_roles_VANGUARD',
       'champ_roles_WARDEN'],
      dtype='object')

In [59]:
# df = s[0]
role_cols = sorted([col for col in df.columns if col.startswith("champ_roles")])
df["champ_roles"]" = tuple(zip(*(df[role_col] for role_col in role_cols)))
df

SyntaxError: unterminated string literal (detected at line 3) (805925794.py, line 3)

In [57]:
role_cols

['champ_roles_ARTILLERY',
 'champ_roles_ASSASSIN',
 'champ_roles_BATTLEMAGE',
 'champ_roles_BURST',
 'champ_roles_CATCHER',
 'champ_roles_DIVER',
 'champ_roles_ENCHANTER',
 'champ_roles_FIGHTER',
 'champ_roles_JUGGERNAUT',
 'champ_roles_MAGE',
 'champ_roles_MARKSMAN',
 'champ_roles_SKIRMISHER',
 'champ_roles_SPECIALIST',
 'champ_roles_SUPPORT',
 'champ_roles_TANK',
 'champ_roles_VANGUARD',
 'champ_roles_WARDEN']

In [30]:
df.columns

Index(['puuid', 'champ_name', 'rating', 'user_id', 'champ_id', 'summoner_rank',
       'summoner_lane', 'champ_adaptive_type', 'champ_attack_type',
       'champ_resource', 'champ_positions', 'champ_roles',
       'champ_positions_BOTTOM', 'champ_positions_JUNGLE',
       'champ_positions_MIDDLE', 'champ_positions_SUPPORT',
       'champ_positions_TOP', 'champ_roles_ARTILLERY', 'champ_roles_ASSASSIN',
       'champ_roles_BATTLEMAGE', 'champ_roles_BURST', 'champ_roles_CATCHER',
       'champ_roles_DIVER', 'champ_roles_ENCHANTER', 'champ_roles_FIGHTER',
       'champ_roles_JUGGERNAUT', 'champ_roles_MAGE', 'champ_roles_MARKSMAN',
       'champ_roles_SKIRMISHER', 'champ_roles_SPECIALIST',
       'champ_roles_SUPPORT', 'champ_roles_TANK', 'champ_roles_VANGUARD',
       'champ_roles_WARDEN'],
      dtype='object')

In [14]:
import torch
role_cols = sorted([col for col in df.columns if col.startswith("champ_roles")])
champ_roles = torch.tensor(df[role_cols].values, dtype=torch.float)

TypeError: can't convert np.ndarray of type numpy.object_. The only supported types are: float64, float32, float16, complex64, complex128, int64, int32, int16, int8, uint64, uint32, uint16, uint8, and bool.

In [18]:
df

puuid champ_name  \
0       --EEhXPKpjfGXqRUXQeFUIrad-z3jgjyrwQj6Z49G4zWAK...     Aatrox   
1       -0tFbkE3vD6takqkFfPNO0xIRQsE-5GeKCJEBRYGwi04RT...     Aatrox   
2       -7e5FbjuTrjsYyDu8GQG0p9wORit7_GD7BHCxR-k9rNo6c...     Aatrox   
3       -AeAsdpxcfQCzruP8eiXWNoatCvBehRa4jQHi8EwcOS-o2...     Aatrox   
4       -Bb1a-1E8rA-pPj9Ox4CMqD9HFhUc621aLpnJCb-L0uHMH...     Aatrox   
...                                                   ...        ...   
146195  _vuXUF_TQs1RuindiNch6El_TrJX9b609fJGbXH64046v3...     Yorick   
146196  _wcrNrVvGYv3syJjVhNZx93SZJOwl3GYn0vK3oOxQb-0Jh...     Yorick   
146197  _xGyR0kT2240JuSOwzokb0ewFGVR3VeeGNJMBsYk3oU6Di...     Yorick   
146198  _Xuv4oW8ZMrsulBBFw8neDnnzf517VhDK9gKsGzUHG5YnS...     Yorick   
146199  _zI3Jacjq9-EgA4Nk-ZSO7KIzac3dgnFEu-qtO-11hBr7L...     Yorick   

          rating  user_id  champ_id summoner_rank summoner_lane  \
0       8.859117        0         0       DIAMOND        MIDDLE   
1       2.290347        1         0   GRANDMASTER        MIDDLE   
2       0.000000        2         0       DIAMOND        JUNGLE   
3       6.300402        3         0       DIAMOND        MIDDLE   
4       5.728852        5         0        MASTER        JUNGLE   
...          ...      ...       ...           ...           ...   
146195  1.861314      501       161   GRANDMASTER           TOP   
146196  0.000000      502       161    CHALLENGER       SUPPORT   
146197  0.000000      503       161       DIAMOND       SUPPORT   
146198  3.870494      495       161       DIAMOND        JUNGLE   
146199  0.000000      504       161    CHALLENGER        MIDDLE   

       champ_adaptive_type champ_attack_type champ_resource champ_positions  \
0          PHYSICAL_DAMAGE             MELEE     BLOOD_WELL           [TOP]   
1          PHYSICAL_DAMAGE             MELEE     BLOOD_WELL           [TOP]   
2          PHYSICAL_DAMAGE             MELEE     BLOOD_WELL           [TOP]   
3          PHYSICAL_DAMAGE             MELEE     BLOOD_WELL           [TOP]   
4          PHYSICAL_DAMAGE             MELEE     BLOOD_WELL           [TOP]   
...                    ...               ...            ...             ...   
146195     PHYSICAL_DAMAGE             MELEE           MANA           [TOP]   
146196     PHYSICAL_DAMAGE             MELEE           MANA           [TOP]   
146197     PHYSICAL_DAMAGE             MELEE           MANA           [TOP]   
146198     PHYSICAL_DAMAGE             MELEE           MANA           [TOP]   
146199     PHYSICAL_DAMAGE             MELEE           MANA           [TOP]   

                        champ_roles  
0       [FIGHTER, JUGGERNAUT, TANK]  
1       [FIGHTER, JUGGERNAUT, TANK]  
2       [FIGHTER, JUGGERNAUT, TANK]  
3       [FIGHTER, JUGGERNAUT, TANK]  
4       [FIGHTER, JUGGERNAUT, TANK]  
...                             ...  
146195  [FIGHTER, JUGGERNAUT, TANK]  
146196  [FIGHTER, JUGGERNAUT, TANK]  
146197  [FIGHTER, JUGGERNAUT, TANK]  
146198  [FIGHTER, JUGGERNAUT, TANK]  
146199  [FIGHTER, JUGGERNAUT, TANK]  

[146200 rows x 12 columns]

In [12]:
df = s[0]

In [14]:
import pandas as pd
from sklearn.preprocessing import MultiLabelBinarizer
categorical_cols = [
    "summoner_rank",
    "summoner_lane",
    "champ_attack_type",
    "champ_adaptive_type",
    # New
    "champ_resource",
]
df[categorical_cols] = (
    OrdinalEncoder().fit_transform(df[categorical_cols]).astype(int)
)

list_cols = ["champ_positions", "champ_roles"]
mlb = MultiLabelBinarizer()
for list_col in list_cols:
    position_onehot = pd.DataFrame(
        mlb.fit_transform(df[list_col]),
        columns=[f"{list_col}_{cls}" for cls in mlb.classes_],
        index=df.index,
    )
    df = pd.concat([df, position_onehot], axis=1)

In [18]:
df.columns

Index(['puuid', 'champ_name', 'rating', 'user_id', 'champ_id', 'summoner_rank',
       'summoner_lane', 'champ_adaptive_type', 'champ_attack_type',
       'champ_resource', 'champ_positions', 'champ_roles',
       'champ_positions_BOTTOM', 'champ_positions_JUNGLE',
       'champ_positions_MIDDLE', 'champ_positions_SUPPORT',
       'champ_positions_TOP', 'champ_roles_ARTILLERY', 'champ_roles_ASSASSIN',
       'champ_roles_BATTLEMAGE', 'champ_roles_BURST', 'champ_roles_CATCHER',
       'champ_roles_DIVER', 'champ_roles_ENCHANTER', 'champ_roles_FIGHTER',
       'champ_roles_JUGGERNAUT', 'champ_roles_MAGE', 'champ_roles_MARKSMAN',
       'champ_roles_SKIRMISHER', 'champ_roles_SPECIALIST',
       'champ_roles_SUPPORT', 'champ_roles_TANK', 'champ_roles_VANGUARD',
       'champ_roles_WARDEN'],
      dtype='object')

In [ ]:
df, le_user, le_champion = await mfp.async_load_encoded_ratings()
categorical_cols = ["summoner_rank", "summoner_lane", "champ_attack_type", "champ_adaptive_type"]
df[categorical_cols] = OrdinalEncoder().fit_transform(df[categorical_cols]).astype(int)

In [ ]:
train_df, test_df = train_test_split(df, test_size=0.2)
train_dataset = ChampionsFeaturesDataset(train_df)
test_dataset = ChampionsFeaturesDataset(test_df)

In [ ]:
train_loader = MultiEpochsDataLoader(train_dataset, batch_size=20, shuffle=True)
test_loader = MultiEpochsDataLoader(test_dataset, batch_size=20, shuffle=True)

In [ ]:

import torch
import torch.nn as nn

In [ ]:
ttr = TwoTowerRecommender()
ttm = TwoTowerModel()

In [ ]:
for a, b, c in train_loader:
    a = a
    b = b
    c = c
    break

In [ ]:
user = (torch.tensor([5]), torch.tensor([2]))

In [ ]:
ttm(a, b)

tensor([5.9841, 5.9841, 5.9841, 8.8454, 8.8454, 5.9841, 5.9841, 8.8454, 5.9841,
        5.9841, 5.9841, 5.9841, 8.8454, 5.9841, 8.8454, 5.9841, 8.8454, 5.9841,
        5.9841, 5.9841], grad_fn=<SumBackward1>)

In [ ]:
puuid = "--EEhXPKpjfGXqRUXQeFUIrad-z3jgjyrwQj6Z49G4zWAK77gXCckScrJ9yxTxy91DXiJXWp_ka1Vg"
summoner_df = df[df["puuid"] == puuid].iloc[0]
rank_ids = torch.tensor(summoner_df["summoner_rank"], dtype=torch.long)
lane_ids = torch.tensor(summoner_df["summoner_lane"], dtype=torch.long)
summoner_tuple = (rank_ids, lane_ids)

In [ ]:
champ_df = df[["champ_name", "champ_attack_type", "champ_adaptive_type"]].drop_duplicates().sort_values(by="champ_name")

# Step 1: Extract model input columns
attack_type_ids = torch.tensor(champ_df["champ_attack_type"].values, dtype=torch.long)
adaptive_type_ids = torch.tensor(champ_df["champ_adaptive_type"].values, dtype=torch.long)

# Step 2: Build champ_tensor_tuple
champ_tensor_tuple = (attack_type_ids, adaptive_type_ids)

In [ ]:
predicted_ratings = ttm(summoner_tuple, champ_tensor_tuple)
champ_order = torch.argsort(predicted_ratings, descending=True)
predicted_ratings_dict = {
    predicted_ratings[champ.item()].item(): le_champion.inverse_transform(
        [champ.item()]
    )[0]
    for champ in champ_order
}

In [ ]:
# champ_df[champ_df["champ_name"].isin(["Zoe","Zyra"])]
predicted_ratings_dict

{8.845425605773926: 'Zeri', 5.984121799468994: 'Zyra'}

In [ ]:
scores = ttm(user, champ_tensor_tuple)
scores

tensor([5.9841, 5.9841, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841,
        8.8454, 8.8454, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841, 8.8454, 5.9841, 5.9841,
        5.9841, 8.8454, 5.9841, 5.9841, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 5.9841, 8.8454, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 8.8454,
        8.8454, 5.9841, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 5.9841, 8.8454, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 5.9841, 5.9841, 8.8454, 5.9841, 5.9841, 5.9841, 5.9841,
        5.9841, 5.9841, 5.9841, 5.9841, 

In [ ]:
ttr.train_and_evaluate_model(ttm, train_loader, test_loader)

Epoch 1, Loss: 371.31629758029567
Test MSE: 349.0486298964699
Epoch 2, Loss: 371.29821391878636
Test MSE: 349.1290726462619
Epoch 3, Loss: 371.2960356498384
Test MSE: 349.1041071587786
Epoch 4, Loss: 371.3208090800756
Test MSE: 349.27582577475346
Epoch 5, Loss: 371.32991223524436
Test MSE: 349.09402936064714
Epoch 6, Loss: 371.2974161155899
Test MSE: 349.05147106762627
Epoch 7, Loss: 371.3048209221027
Test MSE: 349.17107934481504
Epoch 8, Loss: 371.29333136802495
Test MSE: 349.0517142112937
Epoch 9, Loss: 371.3234202082278
Test MSE: 349.060121707771
Epoch 10, Loss: 371.31747973030474
Test MSE: 349.73511183157547
Model training completed in 77.09439849853516 seconds.


In [ ]:
ttm

TwoTowerModel(
  (summoner_tower): SummonerTower(
    (rank_factors): Embedding(10, 8)
    (lane_factors): Embedding(5, 8)
    (mlp): Sequential(
      (0): Linear(in_features=16, out_features=64, bias=True)
      (1): ReLU()
      (2): Linear(in_features=64, out_features=32, bias=True)
      (3): ReLU()
      (4): Linear(in_features=32, out_features=10, bias=True)
    )
  )
  (champ_tower): ChampTower(
    (attack_type_factors): Embedding(2, 8)
    (adaptive_type_factors): Embedding(2, 8)
    (mlp): Sequential(
      (0): Linear(in_features=16, out_features=64, bias=True)
      (1): ReLU()
      (2): Linear(in_features=64, out_features=32, bias=True)
      (3): ReLU()
      (4): Linear(in_features=32, out_features=10, bias=True)
    )
  )
)

In [ ]:
model = TwoTowerModel()
optimizer = torch.optim.Adam(model.parameters(), lr=1e-3)

# To update to negative sampling
criterion = nn.MSELoss()

for epoch in range(1):
    model.train()
    total_loss = 0
    for summoner_factors, champ_factors, ratings in train_loader:
        optimizer.zero_grad()
        preds = model(summoner_factors, champ_factors)
        loss = criterion(preds, ratings)
        loss.backward()
        optimizer.step()
        total_loss += loss.item()
    print(f"Epoch {epoch+1}, Loss: {total_loss / len(train_loader)}")  

[tensor([0, 0, 0, 1, 1]), tensor([0, 1, 1, 1, 1])]
[tensor([1, 1, 0, 1, 1]), tensor([1, 1, 1, 1, 0])]
[tensor([0, 0, 0, 0, 1]), tensor([1, 1, 1, 1, 1])]
[tensor([0, 1, 0, 0, 1]), tensor([1, 1, 0, 0, 0])]
[tensor([0, 1, 1, 1, 1]), tensor([1, 0, 1, 1, 0])]
[tensor([0, 0, 1, 0, 0]), tensor([1, 1, 0, 1, 1])]
[tensor([0, 0, 0, 1, 0]), tensor([1, 0, 1, 0, 0])]
[tensor([0, 0, 0, 0, 0]), tensor([0, 1, 1, 0, 0])]
[tensor([1, 1, 0, 1, 0]), tensor([1, 1, 1, 1, 1])]
[tensor([1, 0, 1, 1, 1]), tensor([0, 0, 1, 0, 0])]
[tensor([0, 1, 1, 0, 0]), tensor([0, 0, 1, 1, 1])]
[tensor([1, 1, 1, 1, 1]), tensor([1, 0, 1, 0, 0])]
[tensor([1, 0, 0, 1, 1]), tensor([1, 1, 1, 0, 0])]
[tensor([1, 0, 0, 1, 0]), tensor([1, 1, 0, 1, 1])]
[tensor([1, 0, 1, 1, 1]), tensor([1, 1, 0, 0, 1])]
[tensor([1, 1, 0, 1, 0]), tensor([0, 0, 1, 0, 1])]
[tensor([0, 1, 1, 1, 0]), tensor([1, 0, 0, 0, 0])]
[tensor([0, 1, 1, 0, 0]), tensor([0, 0, 1, 1, 1])]
[tensor([1, 0, 0, 1, 0]), tensor([0, 1, 0, 0, 1])]
[tensor([1, 1, 0, 1, 1]), tenso

In [ ]:
# Step 1: Build the df with column of lets say mode rank, mode lanes, roles, attack_types
# Step 2: Make train and test loader using TwoTowerChampionDataset
# Step 3: iterate for user_feattures, champ_features, rating in loader: preds = model(user_features, champ_features)

In [ ]:
puuid = "_2dRYSt03dHrJrRDcYImk2_umcnVSo8i-1WMun-j8YAFYk9CzauMu7WjQ8IJCY_RDWMopccQI_qfcw"
match_ids = rah.get_player_matches(puuid)